### Create Lookup features 

We've learned how to define a target and materialize data using observation tables. Now, let's dive into basic feature engineering.

The most straightforward features we can craft with FeatureByte are known as lookup features. These are either direct columns taken from the source table or simple computations that don't require any aggregations.

In [1]:
import featurebyte as fb

# Set your profile to the tutorial environment
fb.use_profile("tutorial")

catalog_name = "Grocery Dataset Tutorial"
catalog = fb.Catalog.activate(catalog_name)  

10:45:57 | WARNING  | Service endpoint is inaccessible: http://featurebyte-server:8088/
10:45:58 | INFO     | Using profile: tutorial
10:45:58 | INFO     | Using configuration file at: /Users/gxav/.featurebyte/config.yaml
10:45:58 | INFO     | Active profile: tutorial (https://tutorials.featurebyte.com/api/v1)
10:45:58 | INFO     | SDK version: 2.0.1.dev67
10:45:58 | INFO     | No catalog activated.
10:45:58 | INFO     | Catalog activated: Grocery Dataset Tutorial


16:07:20 | INFO     | Using configuration file at: /Users/gxav/.featurebyte/config.yaml


16:07:20 | INFO     | Active profile: tutorial (https://tutorials.featurebyte.com/api/v1)


16:07:20 | WARNING  | Remote SDK version (1.1.0.dev7) is different from local (1.1.0.dev1). Update local SDK to avoid unexpected behavior.


16:07:20 | INFO     | No catalog activated.


16:07:20 | INFO     | Catalog activated: Grocery Dataset Tutorial


In [2]:
# Get view from GROCERYCUSTOMER scd table.
grocerycustomer_view = catalog.get_view("GROCERYCUSTOMER")

#### Create Lookup feature

In [3]:
# Create lookup feature from DateOfBirth column for customer entity.
customer_dateofbirth = grocerycustomer_view["DateOfBirth"].as_feature("CUSTOMER_DateOfBirth")

#### Derive Age at the point-in-time of the request observation

In [4]:
# Derive Age from the point-in-time and the date of birth.
customer_age = (
    (fb.RequestColumn.point_in_time() - customer_dateofbirth).dt.day / 365.25
).floor()
# Name feature
customer_age.name = "CUSTOMER_Age"

In [5]:
# Transform age into a 5 year age band.
customer_age_band = (
    ((customer_age + 1) / 5).ceil() - 1
) * 5
customer_age_band = (
    customer_age_band.astype(str)
     + "-" + (customer_age_band + 4).astype(str)
)
# Name feature
customer_age_band.name = "CUSTOMER_Age_band"

#### Preview feature
We will use observation table we created in previous tutorial here.

In [6]:
# Check the primary entity of the feature'
customer_age.primary_entity

 {
   'name': 'customer',
   'created_at': '2024-12-18T02:40:54.536000',
   'updated_at': '2024-12-18T02:40:58.932000',
   'description': None,
   'serving_names': [
     'GROCERYCUSTOMERGUID'
   ],
   'catalog_name': 'Grocery Dataset Tutorial'
 }]

In [7]:
# Get observation table: 'Preview Table with 10 items'
preview_table = catalog.get_observation_table("Preview Table with 10 items")

In [8]:
# Preview CUSTOMER_Age
customer_age.preview(preview_table)

POINT_IN_TIME                GROCERYINVOICEITEMGUID  CUSTOMER_Age
0 2022-12-30 16:42:05  4dd1487a-0379-4eef-b200-97ac1bb1164f            68
1 2022-08-22 06:10:42  9267d0dd-9685-4667-8f06-1761abe73c4d            26
2 2023-06-06 16:13:44  bdc6b6bb-a23a-48c8-bb3a-622d9161c0e8            49
3 2022-07-23 17:33:25  849454c5-6640-419d-871d-1f0895a1c3b4            38
4 2022-09-07 09:16:15  53eac49e-7ecd-4cb6-a1c0-38e3900efd7a            81
5 2023-05-21 13:59:44  989643fe-1377-4f5f-8f38-f349a611da0c            68
6 2022-09-23 18:09:33  459a1b6e-1239-46d1-9e40-539c7e895483            46
7 2023-03-21 13:49:48  84225bbb-adb8-451e-98c0-897c83c2fad9            66
8 2023-03-07 17:53:55  cb478a4e-9266-4523-8ee0-e205881cc5f5            24
9 2023-01-06 08:49:29  dad86e21-3af4-4b5b-8058-60f946b6dac5            54

In [9]:
# Preview CUSTOMER_Age_band
customer_age_band.preview(preview_table)

POINT_IN_TIME                GROCERYINVOICEITEMGUID CUSTOMER_Age_band
0 2022-12-30 16:42:05  4dd1487a-0379-4eef-b200-97ac1bb1164f             65-69
1 2022-08-22 06:10:42  9267d0dd-9685-4667-8f06-1761abe73c4d             25-29
2 2023-06-06 16:13:44  bdc6b6bb-a23a-48c8-bb3a-622d9161c0e8             45-49
3 2022-07-23 17:33:25  849454c5-6640-419d-871d-1f0895a1c3b4             35-39
4 2022-09-07 09:16:15  53eac49e-7ecd-4cb6-a1c0-38e3900efd7a             80-84
5 2023-05-21 13:59:44  989643fe-1377-4f5f-8f38-f349a611da0c             65-69
6 2022-09-23 18:09:33  459a1b6e-1239-46d1-9e40-539c7e895483             45-49
7 2023-03-21 13:49:48  84225bbb-adb8-451e-98c0-897c83c2fad9             65-69
8 2023-03-07 17:53:55  cb478a4e-9266-4523-8ee0-e205881cc5f5             20-24
9 2023-01-06 08:49:29  dad86e21-3af4-4b5b-8058-60f946b6dac5             50-54

In [10]:
# Save features to catalog 
customer_age.save()
customer_age_band.save()

Done! |████████████████████████████████████████| 100% in 6.1s (0.17%/s)         
Done! |████████████████████████████████████████| 100% in 6.1s (0.17%/s)         


Working... |                                        | ▃▅▇ 0% in 0s (~0s, 0.0%/s)

Working... |                                        | ▄▆█ 0% in 0s (~0s, 0.0%/s)

Working... |                                        | ▅▇▇ 0% in 0s (~0s, 0.0%/s)

Working... |                                        | ▆█▆ 0% in 1s (~0s, 0.0%/s)

...

Working... |████████████████████████████████████████| ▂▂▄ 100% in 6s (~0s, 0.2%/

Working... |████████████████████████████████████████| ▁▃▅ 100% in 6s (~0s, 0.2%/

Working... |████████████████████████████████████████| ▂▄▆ 100% in 6s (~0s, 0.2%/

Working... |████████████████████████████████████████| ▃▅▇ 100% in 6s (~0s, 0.2%/

Done! |████████████████████████████████████████| 100% in 6.1s (0.17%/s)         

In [11]:
# Add description
customer_age.update_description("Age of the customer.")
customer_age_band.update_description("Age Band of the customer.")

#### Check feature definition files (same as definition files we discussed in target tutorial)

In [12]:
customer_age.definition

'# Generated by SDK version: 2.0.1.dev119\nfrom bson import ObjectId\nfrom featurebyte import SCDTable\nfrom featurebyte.api.request_column import RequestColumn\n\n\n# scd_table name: "GROCERYCUSTOMER"\nscd_table = SCDTable.get_by_id(ObjectId("676235f3375a850179e42f8c"))\nscd_view = scd_table.get_view(\n    view_mode="manual",\n    drop_column_names=["record_available_at", "CurrentRecord"],\n    column_cleaning_operations=[],\n)\ngrouped = scd_view.as_features(\n    column_names=["DateOfBirth"],\n    feature_names=["CUSTOMER_DateOfBirth"],\n    offset=None,\n)\nfeat = grouped["CUSTOMER_DateOfBirth"]\nrequest_col = RequestColumn.point_in_time()\nfeat_1 = ((request_col - feat).dt.day / 365.25).floor()\nfeat_1.name = "CUSTOMER_Age"\noutput = feat_1\noutput.save(_id=ObjectId("67623766043662b29958c24a"))\n'

In [13]:
customer_age_band.definition

'# Generated by SDK version: 2.0.1.dev119\nfrom bson import ObjectId\nfrom featurebyte import SCDTable\nfrom featurebyte.api.request_column import RequestColumn\n\n\n# scd_table name: "GROCERYCUSTOMER"\nscd_table = SCDTable.get_by_id(ObjectId("676235f3375a850179e42f8c"))\nscd_view = scd_table.get_view(\n    view_mode="manual",\n    drop_column_names=["record_available_at", "CurrentRecord"],\n    column_cleaning_operations=[],\n)\ngrouped = scd_view.as_features(\n    column_names=["DateOfBirth"],\n    feature_names=["CUSTOMER_DateOfBirth"],\n    offset=None,\n)\nfeat = grouped["CUSTOMER_DateOfBirth"]\nrequest_col = RequestColumn.point_in_time()\nfeat_1 = ((request_col - feat).dt.day / 365.25).floor()\nfeat_1.name = "CUSTOMER_Age"\nfeat_2 = ((((feat_1 + 1) / 5).ceil() - 1) * 5).astype(str) + "-"\nfeat_3 = ((((feat_1 + 1) / 5).ceil() - 1) * 5) + 4\nfeat_4 = feat_2 + feat_3.astype(str)\nfeat_4.name = "CUSTOMER_Age_band"\noutput = feat_4\noutput.save(_id=ObjectId("67623766043662b29958c254"))\n'

### Concepts in this tutorial
- [More on features](https://docs.featurebyte.com/latest/about/glossary/#feature-creation)
- [More on lookup features](https://docs.featurebyte.com/latest/about/glossary/#lookup-features)
- [More about point-in-time](https://docs.featurebyte.com/latest/about/glossary/#point-in-time)

#### SDK reference for
- [Feature](https://docs.featurebyte.com/latest/reference/core/feature/)
- [ViewColumn.as_feature()](https://docs.featurebyte.com/latest/reference/featurebyte.api.view.ViewColumn.as_feature/)
- [RequestColumn.point_in_time](https://docs.featurebyte.com/latest/reference/featurebyte.api.request_column.RequestColumn.point_in_time/)
- [Feature.preview()](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.preview/)
- [Feature.save()](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.save/)